OData API

https://oda.ft.dk/Home/OdataQuery

https://www.odata.org/

https://www.ft.dk/-/media/sites/ft/pdf/dokumenter/aabne-data/oda-browser_brugervejledning.ashx

https://www.odata.org/documentation/odata-version-3-0/url-conventions/

https://www.odata.org/documentation/odata-version-3-0/odata-version-3-0-core-protocol/

Source root Link: "https://oda.ft.dk/api/"

ftp://oda.ft.dk/ODAXML/Referat/samling/


## Folketinget data

The data related to the meetings in Folketinget is collected following the guide on Folketinget's homepage:
https://www.ft.dk/-/media/sites/ft/pdf/dokumenter/aabne-data/oda-browser_brugervejledning.ashx.
Transcripts from all meetings going back to 2009 are available for download in xml format using a login described in the guide and some specific ftp software. Because it is interesting to compare topics from Twitter with topics in Folketinget, only the transcripts from the same period as the tweets are used for further analysis. 71% of the available tweets are posted in 2018 and after.

The years in Folketinget do not follow the calender year, as they start and end the first Tuesday of October. So, the meetings from 2018 are actually from October 2017 to October 2018. The data from 2017 are kept for the purpose of having slightly more data and because it is assumed that topics vary little enought for it to still be relevant.

In total 284 meeting stranscripts amounting to 256.6Mb of data has been downloaded and parsed for analysis.

It is not stated how the transcripts are made, however, they are proofread before publication. 


In [16]:
#pip install bs4 lxml

In [71]:
import requests
import urllib.request
import os
import io
import json

import numpy as np
import pandas as pd
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import TfidfVectorizer

from bs4 import BeautifulSoup as bs
from bs4.element import Comment
import lxml

import xml.etree.ElementTree as et 
from xml.dom import minidom

import re

import dateutil
import datetime as dt
from dateutil.easter import *
from dateutil.rrule import *
from dateutil.parser import *
from datetime import *

In [2]:
path = os.getcwd()

In [3]:
path = path+'/samling/'

# Parsing XML

In [92]:
i = 1
for subdir, dir, files in os.walk(path):
    for file in files:
        filepath = subdir+'/' + file
        if filepath.endswith(".xml") and i == 1:
            xmlTree = et.parse(filepath)

            
elemList = []

for elem in xmlTree.iter():
    elemList.append(elem.tag)

# now I remove duplicities - by convertion to set and back to list
#elemList = list(set(elemList))

# Just printing out the result
from collections import Counter
Counter(elemList)

Counter({'Dokument': 1,
         'MetaMeeting': 1,
         'ParliamentarySession': 1,
         'ParliamentaryGroup': 1,
         'MeetingNumber': 1,
         'DateOfSitting': 1,
         'Location': 1,
         'EdixiDocLocation': 1,
         'AudioFileFolder': 1,
         'TitelGruppe': 1,
         'Titel': 1,
         'Linea': 126,
         'Char': 138,
         'UnderTitel': 1,
         'DagsordenPlan': 1,
         'Rubrica': 10,
         'PunktTekst': 8,
         'Exitus': 72,
         'DagsordenPunkt': 5,
         'MetaFTAgendaItem': 5,
         'ItemNo': 5,
         'FTCase': 5,
         'FTCaseNumber': 5,
         'FTCaseType': 5,
         'FTCaseStage': 5,
         'ShortTitle': 5,
         'Aktivitet': 10,
         'Tale': 12,
         'Taler': 12,
         'MetaSpeakerMP': 12,
         'OratorFirstName': 12,
         'OratorLastName': 12,
         'GroupNameShort': 12,
         'OratorRole': 12,
         'TalerTitel': 12,
         'TaleSegment': 12,
         'MetaSpeechSegme

In [93]:
starttid_vec = []
sluttid_vec=[]
navn_vec = []
efternavn_vec = []
tekst_vec = []
parti_vec = []
rolle_vec = []

# Go through all the folders and files containing transcripts
for subdir, dir, files in os.walk(path):
    for file in files:
        filepath = subdir+'/' + file
        if filepath.endswith(".xml"):
            tree = et.parse(filepath)
            root = tree.getroot() 

            # Do this if the speaker has an associated party, i.e. not a minister or the chairman
            for speech in root.iter('Tale'):
                tags=[node.tag for node in speech.iter()]
                if('TekstGruppe' in tags):
                    if('GroupNameShort' in tags):
                        for node in speech.iter():
                            if(node.tag == 'StartDateTime'):
                                starttid_vec.append(node.text)
                            elif(node.tag == 'OratorFirstName'):
                                navn_vec.append(node.text)
                            elif(node.tag == 'OratorLastName'):
                                efternavn_vec.append(node.text)
                            elif(node.tag == 'OratorRole'):
                                rolle_vec.append(node.text)
                            elif(node.tag=='TekstGruppe'):
                                # This tag is preculiar, as there are multiple children ending with 'Char' as the youngest.
                                # Concate all text within 'TekstGruppe'.
                                tekstgruppe = ''
                                for k in node.iter():
                                    if k.tag=="Char":
                                        tekstgruppe+=' '+k.text
                                tekst_vec.append(tekstgruppe)
                            elif(node.tag=='GroupNameShort'):
                                parti_vec.append(node.text)

                            # If there are more text than speaker names, remove the excess.
                            # We will loose a few pieces of text but only around 1%
                            if len(tekst_vec)>len(navn_vec):
                                tekst_vec.pop()
                            if len(starttid_vec)>len(navn_vec):
                                starttid_vec.pop()
                                
                    # Do this if the speaker is either a minister or the chairman
                    else:
                        parti_vec.append('Ukendt')
                        for node in speech.iter():
                            if(node.tag == 'StartDateTime'):
                                starttid_vec.append(node.text)
                            elif(node.tag == 'OratorFirstName'):
                                navn_vec.append(node.text)
                            elif(node.tag == 'OratorLastName'):
                                efternavn_vec.append(node.text)
                            elif(node.tag == 'OratorRole'):
                                rolle_vec.append(node.text)
                            elif(node.tag=='TekstGruppe'):
                                # This tag is preculiar, as there are multiple children ending with 'Char' as the youngest.
                                # Concate all text within 'TekstGruppe'.
                                tekstgruppe = ''
                                for k in node.iter():
                                    if k.tag=="Char":
                                        tekstgruppe+=' '+k.text
                                tekst_vec.append(tekstgruppe)
                                
                            # If there are more text than speaker names, remove the excess.
                            # We will loose a few pieces of text but only around 1%
                            if len(tekst_vec)>len(navn_vec):
                                tekst_vec.pop()
                            if len(starttid_vec)>len(navn_vec):
                                starttid_vec.pop()

# Add everuthing to a dictionary and transform it into a Pandas dataframe
dictionary= {'StartDateTime':starttid_vec,'OratorFirstName':navn_vec,'OratorLastName':efternavn_vec,
                 'GroupNameShort':parti_vec,'OratorRole':rolle_vec ,'TekstGruppe':tekst_vec} # 'EndDateTime':sluttid_vec,
df = pd.DataFrame(dictionary)

print('In total, there are {} lines of text in the meetings.'.format(len(df)))
#df.to_csv(path[0:26]+'csv')

In total, there are 143075 lines of text in the meetings.


In [5]:
df.head()

StartDateTime OratorFirstName OratorLastName GroupNameShort  \
0  2019-02-27T13:00:08             Pia     Kjærsgaard             DF   
1  2019-02-27T13:01:34             Pia     Kjærsgaard             DF   
2  2019-02-27T13:01:43             Pia     Kjærsgaard             DF   
3  2019-02-27T13:01:45       Christian      Langballe             DF   
4  2019-02-27T13:02:05             Pia     Kjærsgaard             DF   

  OratorRole                                        TekstGruppe  
0    formand                                    Mødet er åbnet.  
1    formand   Det første spørgsmål er til justitsministeren...  
2    formand                  Værsgo for at oplæse spørgsmålet.  
3     medlem   Spørgsmålet lyder: Vil regeringen stå fast på...  
4    formand                                Værsgo, ministeren.

In [96]:
### Cleaning the data ###

# The chariman (formand) does not add value to the context as he or she only moderates the debate
# by passing on the word from person to person.
# Also some meta data is contained regarding when the meeting ended (MødeSlut). This is also irrelevant.
df=df[df['OratorRole']!='formand']
df=df[df['OratorRole']!='MødeSlut']
df.reset_index(drop=True,inplace=True)

# Generating a column of the full name of the speakers
df['FullName'] = df['OratorFirstName']+' '+df['OratorLastName']

# Making start time into datetime64 format
df['StartDateTime'] = df['StartDateTime'].apply(lambda x: dateutil.parser.parse(x))

In [106]:
df_agg_parti = df.groupby(['GroupNameShort', df['StartDateTime'].dt.year, df['StartDateTime'].dt.month, df['StartDateTime'].dt.day])['TekstGruppe'].apply(lambda x : ' '.join(x))
test = pd.DataFrame(df_agg_parti)#.sort_values([df['StartDateTime'].dt.month])

In [107]:
test.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 2220 entries, ('ALT', 2018, 10, 4) to ('V', 2020, 12, 2)
Data columns (total 1 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   TekstGruppe  2220 non-null   object
dtypes: object(1)
memory usage: 26.8+ KB


In [11]:
df_agg_navn = df.groupby(['FullName'])['TekstGruppe'].apply(lambda x : ' '.join(x))
#df = df.drop_duplicates()

FullName
Aaja Chemnitz Larsen      Mange tak. Inuit Ataqatigiit støtter også lov...
Aki-Matilda Høegh-Dam     Tak for det. Først har jeg en kort kommentar ...
Aleqa Hammond             Grønland er i forandring, rigsfællesskabet er...
Alex Ahrendtsen           Tak. Det åbne spørgsmål er jo, hvad Socialdem...
Alex Vanopslagh           (Talen er under udarbejdelse)  (Talen er unde...
                                               ...                        
Victoria Velasquez        Tak for det. Det her ændringsforslag handler ...
Villum Christensen        Tak for det. Lad mig starte med at sige, at L...
Yildiz Akdogan            Tak for det, formand. Enhedslisten ønsker med...
Zenia Stampe              Tak for det. Der er jo ingen tvivl om, at sko...
Øjvind Vilsholm           Ordføreren siger, at hovedbegrundelsen for at...
Name: TekstGruppe, Length: 263, dtype: object

In [62]:
df.head()

level_0  index       StartDateTime OratorFirstName OratorLastName  \
0        0      0 2019-02-27 13:01:45       Christian      Langballe   
1        1      1 2019-02-27 13:02:06      Søren Pape        Poulsen   
2        2      2 2019-02-27 13:03:40       Christian      Langballe   
3        3      3 2019-02-27 13:04:55      Søren Pape        Poulsen   
4        4      4 2019-02-27 13:05:49       Christian      Langballe   

  GroupNameShort OratorRole  \
0             DF     medlem   
1           None   minister   
2             DF     medlem   
3           None   minister   
4             DF     medlem   

                                         TekstGruppe             FullName  
0   Spørgsmålet lyder: Vil regeringen stå fast på...  Christian Langballe  
1   Tak for det. Og tak for spørgsmålet. Fremmedk...   Søren Pape Poulsen  
2   Det står tilbage at få besvaret nogle ting i ...  Christian Langballe  
3   Tak. Jeg skal prøve, så godt jeg kan – det va...   Søren Pape Poulsen  
4   Altså, jeg synes jo, at de her burkabrude, so...  Christian Langballe

In [58]:
df.reset_index(inplace=True, drop=True)

In [68]:
df.drop(labels=['level_0'], axis=1, inplace=True)

In [69]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 68445 entries, 0 to 68444
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   index            68445 non-null  int64         
 1   StartDateTime    68445 non-null  datetime64[ns]
 2   OratorFirstName  68215 non-null  object        
 3   OratorLastName   68215 non-null  object        
 4   GroupNameShort   55527 non-null  object        
 5   OratorRole       68215 non-null  object        
 6   TekstGruppe      68445 non-null  object        
 7   FullName         68215 non-null  object        
dtypes: datetime64[ns](1), int64(1), object(6)
memory usage: 4.2+ MB


## Topics

In [15]:
stopwords = open('stopord.txt').read().splitlines() #Link: https://gist.github.com/berteltorp/0cf8a0c7afea7f25ed754f24cfc2467b

In [31]:
# convert the text to a tf-idf weighted term-document matrix

# Hyperparameters
corpus = 2000000 #Der er ca. ? forskellige ord, efter stopord
l1_ratio = 0
max_iter = 50000
no_components = 5

min_df = 2
max_df = 0.6

data=df['TekstGruppe']

vectorizer = TfidfVectorizer(max_features=corpus, min_df=min_df, max_df=max_df, stop_words=stopwords)

X = vectorizer.fit_transform(data)
 
idx_to_word = np.array(vectorizer.get_feature_names())


# apply Non-negative Matrix Factorization to get topics using TF-IDF
nmf = NMF(n_components=no_components, solver="mu", l1_ratio = l1_ratio, max_iter = max_iter, random_state=1)

W = nmf.fit_transform(X)

H = nmf.components_
 
# print the topics
 
for i, topic in enumerate(H):
 
    print("Topic {}: {}".format(i + 1, ", ".join([str(x) for x in idx_to_word[topic.argsort()[-10:]]])))

Topic 1: tale, enig, sagde, sf, egentlig, tænke, spørge, høre, talen, udarbejdelse
Topic 2: gang, arbejde, går, penge, spørgsmål, står, venstre, år, regeringen, forhold
Topic 3: europa, tyrkiet, land, folkeparti, statsborgerskab, lande, danske, dansk, danmark, eu
Topic 4: lyder, svare, forretningsordens, spørgsmål, punktet, dagsordenen, taget, spørgeren, spørgsmålet, udgået
Topic 5: barnets, mennesker, familier, barnet, forældrene, barn, børnene, unge, forældre, børn


In [32]:
idx_to_word

array(['00', '000', '000001', ..., 'øvre', 'øvrig', 'øvrige'],
      dtype='<U36')

In [33]:
vectorizer

TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
                dtype=<class 'numpy.float64'>, encoding='utf-8',
                input='content', lowercase=True, max_df=0.6,
                max_features=2000000, min_df=2, ngram_range=(1, 1), norm='l2',
                preprocessor=None, smooth_idf=True,
                stop_words=['ad', 'af', 'aldrig', 'alene', 'alle', 'allerede',
                            'alligevel', 'alt', 'altid', 'anden', 'andet',
                            'andre', 'at', 'bag', 'bare', 'begge', 'bla',
                            'blandt', 'blev', 'blive', 'bliver', 'burde', 'bør',
                            'ca', 'da', 'de', 'dem', 'den', 'denne', 'dens', ...],
                strip_accents=None, sublinear_tf=False,
                token_pattern='(?u)\\b\\w\\w+\\b', tokenizer=None, use_idf=True,
                vocabulary=None)

In [34]:
print(topic.argsort()[-10:])
print(idx_to_word[topic.argsort()[-10:]])

[ 4829 36375 14555  4828 18677  4809  8928 62161 18621  8814]
['barnets' 'mennesker' 'familier' 'barnet' 'forældrene' 'barn' 'børnene'
 'unge' 'forældre' 'børn']


In [38]:
for i in range(len(W)):
    print(W[i])

[3.87989045e-10 7.43324240e-03 4.87626543e-02 2.40827974e-02
 2.46006959e-03]
[5.68485892e-10 1.15002570e-02 6.52783281e-02 7.31746281e-03
 9.35574757e-03]
[2.73240358e-05 2.17737314e-02 3.16548938e-02 5.83522310e-03
 5.20307556e-03]
[5.44963658e-08 1.14746016e-02 1.08222931e-02 0.00000000e+00
 2.86379224e-02]
[1.05615646e-07 3.15346354e-03 1.08806341e-02 0.00000000e+00
 1.90338916e-02]
[1.99299266e-07 4.66495504e-03 6.90608006e-03 0.00000000e+00
 4.06933783e-02]
[2.65814103e-07 8.94556909e-03 1.32650366e-02 0.00000000e+00
 6.57434171e-03]
[1.04792226e-08 1.03053180e-02 4.69302295e-02 0.00000000e+00
 8.67502688e-03]
[3.54906125e-14 5.90060029e-03 2.40399630e-03 2.50459784e-02
 2.60759657e-07]
[1.40807935e-08 1.30341506e-02 1.53290150e-03 3.94471642e-02
 9.11123639e-04]
[4.65853775e-11 1.02908063e-02 3.47941319e-03 9.88556316e-07
 1.39167592e-03]
[1.93172855e-05 2.06314148e-02 0.00000000e+00 1.46109013e-02
 4.30878727e-05]
[6.80044601e-11 1.84428228e-02 0.00000000e+00 2.07180043e-09
 3.

[2.53930919e-16 2.96483575e-03 0.00000000e+00 3.69599632e-12
 1.96943406e-04]
[1.91469755e-13 7.78854893e-03 4.89694280e-03 0.00000000e+00
 3.58213869e-03]
[6.84150149e-06 2.24785677e-03 0.00000000e+00 0.00000000e+00
 3.61298931e-02]
[3.72796355e-07 1.98119342e-02 0.00000000e+00 2.08954609e-11
 8.95337640e-03]
[5.05194340e-10 8.10089709e-03 0.00000000e+00 0.00000000e+00
 4.86591053e-03]
[1.81394449e-09 2.55185754e-02 0.00000000e+00 5.83591031e-07
 3.77296855e-03]
[5.05854393e-10 7.23332620e-03 0.00000000e+00 6.05018100e-06
 1.83318914e-03]
[5.34700137e-07 1.04367334e-02 0.00000000e+00 3.64662866e-07
 1.98707485e-03]
[4.28752126e-11 9.23296751e-03 0.00000000e+00 6.09262685e-06
 6.31827874e-06]
[6.44822240e-06 1.30631500e-02 1.05622984e-02 1.21269661e-11
 1.76965957e-03]
[4.10329271e-08 1.25168219e-02 7.11536507e-03 1.03708641e-06
 1.87446209e-03]
[1.75891912e-06 1.30669726e-03 0.00000000e+00 1.64041314e-11
 5.90433367e-03]
[9.06669633e-08 3.20675565e-02 0.00000000e+00 0.00000000e+00
 8.

 3.14330549e-03]
[8.14728425e-07 1.55082182e-02 0.00000000e+00 9.24667203e-08
 4.48079581e-03]
[1.02041297e-05 1.40060448e-02 0.00000000e+00 4.78703465e-03
 3.12927446e-03]
[2.20983413e-06 5.02285411e-03 2.52951396e-03 0.00000000e+00
 1.20702790e-03]
[8.72807158e-06 2.80801258e-02 0.00000000e+00 0.00000000e+00
 3.29052282e-02]
[1.80016832e-06 1.92577808e-02 0.00000000e+00 7.22395118e-04
 6.57799732e-04]
[1.32417385e-06 1.46659547e-02 0.00000000e+00 0.00000000e+00
 1.16048973e-02]
[6.24189311e-08 1.65845171e-02 5.85567488e-03 0.00000000e+00
 6.79043118e-03]
[3.57609144e-07 1.04264149e-02 0.00000000e+00 0.00000000e+00
 7.81043447e-03]
[5.83530865e-05 1.75457009e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[3.75730610e-07 2.05445072e-02 0.00000000e+00 0.00000000e+00
 1.62572820e-03]
[2.79163272e-06 1.94507770e-02 0.00000000e+00 0.00000000e+00
 1.68593763e-02]
[1.84315588e-06 2.42512314e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[4.23013725e-05 1.35319078e-02 7.07062981e-03 7

 1.60395167e-03]
[9.14024053e-07 4.25199190e-02 0.00000000e+00 0.00000000e+00
 5.18391778e-03]
[9.04969007e-07 2.66312353e-02 0.00000000e+00 0.00000000e+00
 3.55369467e-03]
[3.63265434e-12 1.25366268e-02 0.00000000e+00 2.23757815e-04
 1.58255009e-03]
[3.84896504e-07 2.16416399e-02 2.13656956e-03 0.00000000e+00
 0.00000000e+00]
[2.09707823e-08 1.09727173e-02 0.00000000e+00 3.85837414e-04
 1.56222754e-03]
[8.19419833e-07 3.82575669e-02 0.00000000e+00 0.00000000e+00
 4.21131192e-03]
[2.08578784e-05 2.43864114e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[7.79652685e-06 1.88512339e-02 7.72940329e-03 0.00000000e+00
 3.10276923e-03]
[2.64397973e-06 2.35775388e-02 0.00000000e+00 8.60239238e-05
 0.00000000e+00]
[1.00580351e-06 1.42563924e-02 0.00000000e+00 0.00000000e+00
 3.10371804e-03]
[1.02485904e-07 3.04459247e-02 0.00000000e+00 0.00000000e+00
 2.57016127e-02]
[2.09716286e-08 2.85175293e-02 0.00000000e+00 7.33206333e-07
 5.98030271e-04]
[1.23358609e-05 1.23086826e-02 0.00000000e+00 0

 0.00000000e+00]
[1.24443303e-08 1.59962865e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[3.19413567e-07 2.95753533e-02 0.00000000e+00 5.38168033e-08
 0.00000000e+00]
[3.66163560e-07 1.69963791e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[2.08880827e-05 1.83951576e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.85904303e-07 2.56491691e-02 0.00000000e+00 1.81686305e-07
 0.00000000e+00]
[1.96958739e-06 1.79450264e-02 0.00000000e+00 8.39886161e-03
 1.34864142e-06]
[1.16628307e-15 5.22713002e-03 0.00000000e+00 1.03552514e-02
 0.00000000e+00]
[8.54089748e-06 8.93745363e-03 0.00000000e+00 1.11701845e-03
 0.00000000e+00]
[2.51423712e-05 1.53387301e-02 0.00000000e+00 5.35264131e-06
 0.00000000e+00]
[1.18537208e-02 6.10775538e-03 0.00000000e+00 9.86175361e-06
 0.00000000e+00]
[1.62509277e-05 1.15044978e-02 0.00000000e+00 3.51464483e-06
 0.00000000e+00]
[1.51452383e-06 1.60476336e-02 0.00000000e+00 7.22772208e-03
 3.03011858e-04]
[5.98040497e-08 1.61197351e-02 0.00000000e+00 1

...

 0.00000000e+00]
[1.56279051e-05 1.40947907e-02 3.19350757e-02 4.68439141e-06
 0.00000000e+00]
[2.57042214e-09 2.48094146e-02 0.00000000e+00 1.38973373e-07
 0.00000000e+00]
[1.95411026e-07 2.94977376e-02 0.00000000e+00 9.62081091e-07
 0.00000000e+00]
[4.34525251e-07 2.71519881e-02 0.00000000e+00 1.79889403e-05
 0.00000000e+00]
[2.68963484e-06 1.29677570e-02 0.00000000e+00 5.39883320e-07
 0.00000000e+00]
[5.52661436e-07 2.49176612e-02 0.00000000e+00 2.31098906e-06
 0.00000000e+00]
[4.41646484e-08 1.53204826e-02 7.04637137e-03 0.00000000e+00
 0.00000000e+00]
[1.57554884e-05 3.37960576e-02 0.00000000e+00 8.16121919e-04
 0.00000000e+00]
[4.13537847e-08 2.82775669e-02 8.41385352e-03 2.69216607e-06
 0.00000000e+00]
[8.40252079e-09 1.43607619e-02 1.44197249e-02 0.00000000e+00
 0.00000000e+00]
[2.17771678e-06 2.41312906e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[6.81301216e-09 8.49498631e-03 0.00000000e+00 5.46987871e-03
 1.38227499e-04]
[7.02271445e-06 1.62629156e-02 0.00000000e+00 1

[2.49047463e-05 2.45768482e-02 0.00000000e+00 2.00289621e-07
 0.00000000e+00]
[1.01094936e-05 3.35108939e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.76547897e-06 2.24413544e-02 0.00000000e+00 1.55164149e-08
 0.00000000e+00]
[1.31814562e-05 2.92450164e-02 0.00000000e+00 5.93724289e-05
 0.00000000e+00]
[6.36721254e-07 2.33535943e-02 0.00000000e+00 2.74000252e-02
 9.30850516e-07]
[5.56832338e-06 2.63427336e-02 0.00000000e+00 4.00817829e-07
 0.00000000e+00]
[1.07540716e-08 2.33904491e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.21962353e-07 2.79731180e-02 1.06008894e-02 0.00000000e+00
 0.00000000e+00]
[5.53729316e-08 2.85925066e-02 1.11803447e-02 1.27868786e-03
 3.14641612e-03]
[1.56613810e-05 1.21173519e-02 0.00000000e+00 2.68622709e-05
 0.00000000e+00]
[1.51461268e-12 1.71424605e-02 1.56156712e-02 2.17176566e-04
 0.00000000e+00]
[2.24526810e-05 2.01987892e-02 0.00000000e+00 5.54011127e-06
 4.86925774e-06]
[2.06748165e-05 1.27326163e-02 6.79457176e-03 3.47067409e-05
 1.

 1.84314600e-03]
[2.16251420e-05 8.10336546e-03 0.00000000e+00 5.03029623e-06
 2.05388414e-03]
[4.47075231e-08 2.33341180e-02 0.00000000e+00 5.45018335e-08
 0.00000000e+00]
[7.41802780e-06 1.66570903e-02 0.00000000e+00 8.35962079e-03
 7.56899883e-04]
[1.75696630e-11 1.36538455e-02 3.88227719e-03 6.23955340e-12
 5.10387566e-03]
[7.91209537e-06 2.16504621e-02 0.00000000e+00 4.21407778e-07
 0.00000000e+00]
[5.92311902e-06 2.77198865e-02 0.00000000e+00 5.24975105e-08
 0.00000000e+00]
[1.00419777e-08 5.18967413e-03 0.00000000e+00 0.00000000e+00
 1.24247005e-03]
[6.71998367e-06 1.16830341e-02 0.00000000e+00 1.01754986e-03
 3.68719746e-02]
[4.83648472e-07 1.15384702e-02 0.00000000e+00 0.00000000e+00
 5.50175962e-02]
[4.25889754e-09 1.31976652e-02 0.00000000e+00 0.00000000e+00
 6.33905437e-02]
[5.53549154e-08 1.92399383e-02 0.00000000e+00 0.00000000e+00
 4.36734633e-02]
[5.64779870e-08 7.53644241e-03 0.00000000e+00 0.00000000e+00
 4.63343908e-02]
[7.43861461e-06 9.66612501e-03 0.00000000e+00 0

 4.19370841e-02]
[1.25953557e-08 3.90688338e-03 0.00000000e+00 0.00000000e+00
 1.03224727e-01]
[1.34384187e-05 1.23885102e-02 4.60353014e-04 0.00000000e+00
 0.00000000e+00]
[2.94724603e-07 1.21817521e-02 0.00000000e+00 0.00000000e+00
 3.08665914e-02]
[6.04278346e-05 3.57399293e-03 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.72098962e-06 1.85153877e-02 0.00000000e+00 6.13128472e-03
 0.00000000e+00]
[8.89251185e-07 1.63954278e-02 2.84599777e-03 0.00000000e+00
 0.00000000e+00]
[7.67903677e-08 1.25349993e-02 0.00000000e+00 0.00000000e+00
 3.62280921e-02]
[7.98281372e-06 1.29797622e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.88343946e-06 8.56900849e-04 0.00000000e+00 0.00000000e+00
 6.47420352e-02]
[9.78935266e-09 5.97010140e-03 0.00000000e+00 1.64350775e-04
 2.50452356e-11]
[1.13969187e-08 4.95722610e-03 0.00000000e+00 4.30205847e-08
 5.97856331e-08]
[2.27400560e-05 1.85510999e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.37359727e-07 5.48224758e-05 0.00000000e+00 0

[0.00728034 0.02359615 0.         0.         0.        ]
[5.92237895e-06 1.79664313e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[4.39231615e-06 1.12671070e-02 0.00000000e+00 1.38204584e-04
 0.00000000e+00]
[3.97583613e-06 1.69955560e-02 0.00000000e+00 1.36396873e-02
 3.16797179e-04]
[2.57739681e-05 2.62649146e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[3.42005272e-05 1.58546580e-02 0.00000000e+00 1.80468184e-02
 0.00000000e+00]
[3.94433775e-06 2.56866096e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[6.73892959e-11 1.15610680e-02 0.00000000e+00 2.53283691e-09
 0.00000000e+00]
[6.04479332e-08 1.19235195e-02 0.00000000e+00 6.54630206e-08
 0.00000000e+00]
[3.96275401e-06 2.22661628e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.99770562e-06 1.90793394e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[1.69077931e-07 1.93713304e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[8.15685210e-06 1.58756764e-02 0.00000000e+00 0.00000000e+00
 0.00000000e+00]
[2.1663

In [36]:
for i in range(len(H)):
    print(H[i])

[7.10065934e-05 1.12331977e-05 3.12661627e-36 ... 1.10431829e-23
 1.55292708e-31 7.66606195e-08]
[1.49332215e-02 2.93405507e-01 1.12797917e-09 ... 6.79318463e-03
 1.35348592e-03 6.30437554e-02]
[0.00488116 0.         0.0009883  ... 0.00255522 0.00076961 0.02566899]
[7.27696301e-08 0.00000000e+00 1.92918891e-08 ... 0.00000000e+00
 0.00000000e+00 3.52050276e-03]
[0.0025398 0.        0.        ... 0.        0.        0.       ]


In [46]:
print(data.shape)
print(W.shape)

print(H.shape)
print(idx_to_word.shape)

(68445,)
(68445, 5)
(5, 66247)
(66247,)


In [37]:
idx_to_word[topic.argsort()[-10:]]

array(['barnets', 'mennesker', 'familier', 'barnet', 'forældrene', 'barn',
       'børnene', 'unge', 'forældre', 'børn'], dtype='<U36')

In [ ]:
# Write to a .csv file

#with open('topics_and_weights.csv', 'w', newline='', encoding='utf-16') as csvfile:
 #   topicwriter = csv.writer(csvfile, delimiter=',',
  #                          quotechar='"', quoting=csv.QUOTE_MINIMAL)
# Create the header
   # topicwriter.writerow(['Topic','Word','Weight'])

In [ ]:
# print the topics for tableau
 
#for i, topic in enumerate(H):
 
 #   max_weights = topic.argsort()[-10:]
  #  words = [str(x) for x in idx_to_word[topic.argsort()[-10:]]]
     
   # for count, item in enumerate(max_weights):
        
    #    with open('topics_and_weights.csv', 'a', newline='', encoding='utf-16') as csvfile:
     #       topicwriter = csv.writer(csvfile, delimiter=',',
      #                      quotechar='"', quoting=csv.QUOTE_MINIMAL)
       #     topicwriter.writerow(["Topic"+str(i+1) ,words[count],H[i,item]])

In [ ]:
#stopwords_edit = open('stopord.txt','a')
#stopwords_edit.write('\nenhedslisten')
#stopwords_edit.close()